# Data Analysis in polars Courselet

**Authors:** 
 - Siddarth Vijayakumar Sivakala (Z2061678@students.niu.edu)
 - David Koop (dakoop@niu.edu)

**Last Updated:** 2025-09-19

This courselet provides background information on using the polars library in python. It focuses on operations designed to wrangle data but includes a number of details on using polars to load, structure, and query data. There are exercises throughout as well as a challenging final part to test your skills. We will use the City of Chicago's [Food Inspection Data](https://data.cityofchicago.org/Health-Human-Services/Food-Inspections/4ijn-s7e5) for this courselet.

This first cell loads a specific subset of data from the food inspection data.

In [ ]:
# Changing the way the jupyter files react to expressions hence displaying the last assigned value in the cell.
%config InteractiveShell.ast_node_interactivity = 'last_expr_or_assign'

In [ ]:
# This segment is used to download the ZIP file of the dataset from online source.

import urllib.request
import gzip

url = "https://data.cityofchicago.org/resource/4ijn-s7e5.csv?"
params = {
    "$where": "2000000 <= inspection_id AND inspection_id <= 2500000",
    "$limit": "100000",
}
encoded_params = urllib.parse.urlencode(params)
# print(url + encoded_params)
request = urllib.request.Request(url + encoded_params)
request.add_header("accept-encoding", "gzip")
with urllib.request.urlopen(request) as response:
    if response.info().get("Content-Encoding") == "gzip":
        with open("Food_Inspections.csv.gz", "wb") as f:
            f.write(response.read())
    else:
        with gzip.open("Food_Inspections.csv.gz", "wb") as f:
            f.write(response.read())

### Reading Data

Polars has a number of way to read data, supporting a variety of data formats. Some of the most frequently used methods are 

- `read_excel` - Reads MS Office Spreadsheets. It requires [`fastexcel`](https://pypi.org/project/fastexcel/) library to be installed which is used as a engine for processing excel files and Apache PyArrow [`pyarrow`](https://arrow.apache.org/docs/python/install.html) for processing the data as rows and columns.

- `read_csv` - Reads Comma Separated Values. Text based data that are separated by commas, the attributes are separated by commas and each attribute is enclosed by a double quotes. Because this is a text-based format, there is no type information provided. Polars will inspect the columns and infer the appropriate data types upon creation or reading of data.

- `read_database` - Reads data from database such as `Mysql` and `Postgresql`. These connections require external libraries to be installed which is used fopr creating an  URI which connects to the corresponding database. One popular method in retriving large data is using [`SQLAlchemy`](https://pypi.org/project/SQLAlchemy/) which acts as both a toolkit and Object Relational Mapper (ORM) and a connection module such as [`PyMySQL`](https://pypi.org/project/PyMySQL/) which is a light weight connector.

- `read_json` - JavaScript Object Notation. A textual format that mimics the specification of nested objects and lists in JavaScript, but limits values to literals. While it does not store type information, it can be paired with a schema and some information can be inferred from the representation (numeric values are specified without strings, for example)

- `read_parquet` - Apache parquet is a  open-source column oriented data storage format. read_parquet function uses its Rust-native Parquet reader by default. Also supports pyarrow based parquet reader.

Polars can read some compressed formats, including gzipped csv files, without the need to first decompress them.

First, we need to import the `polars` library. There is a convention to abbreviate `polars` as `pl`, and we will use this convention in this notebook. We can read the Chicago Food Inspections data directly using the `read_csv` method and its support for gzipped files.

In [ ]:
import polars as pl

df = pl.read_csv("Food_Inspections.csv.gz")

The output, called a **data frame**, looks like a sheet from a spreadsheet program or perhaps a table. It shows the shape (number of rows and columns) in the upper-left corner and then bold header rows show the *name* and *data type* for the column. Because we are reading from a csv file which has no type information, polars *infers* type information for each column from the values in the column. Then, a subset of values are listed; by default, these are the first and last five rows from the dataframe.

If you have used pandas before, note that there are a few differences that you may notice already:

1. *Faster Execution.*  Polars utilizes all the available computing cores in a system whereas Pandas can be restricted to a single core
2. *No Index.* A polars dataframe does not have have index (shown in pandas as the left-most column(s) in bold). This means that extracting rows generally relies on a query instead of key-based access.

A single column can be extracted from the dataframe using the using brackets, e.g. `df['dba_name']`, or using `select()` method, e.g. `df.select('dba_name')`.

In [ ]:
df["results"]

In [ ]:
df.select("results")

##### Exercise

What is the difference between these two methods?

##### Solution

Using brackets returns a series while using the select method returns a dataframe with a single column.

In [ ]:
type(df["results"]), type(df.select("results"))

##### Exercise

You can project multiple columns at once by passing a list to the subscript operator. Try extracting both the `dba_name` column and the `results` column. What is the type of that result? Does `select` also work for multiple columns?

In [ ]:
# Your code here

##### Solution

In [ ]:
df[["results", "dba_name"]]

In [ ]:
type(df[["results", "dba_name"]])

In [ ]:
df.select("results", "dba_name")

### Extracting Data Items

Polars supports row access, but it is not designed to process items row by row. **Try to avoid iterating through items**! You can access a single row using bracket notation and multiple rows using slicing, similar to sequences in Python.

In [ ]:
df[0]

In [ ]:
df[0:1]

In [ ]:
df[1:4]

Note that there is no difference between `df[0]` and `df[0:1]` in polars. (In pandas, the first returns a series and the second a dataframe).

You can also examine just the beginning and end of a dataframe using the `head` and `tail` methods, which take an optional argument for the number of rows to show.

In [ ]:
df.head()

In [ ]:
df.tail(3)

You can also use the `row` method to access an individual items as a *tuple*, However, do not use this method to iterate through a dataframe. If you absolutely need that functionality, use `iter_rows`.

In [ ]:
df.row(3)

You can also used the `named` keyword argument to receive a dictionary instead of a tuple.

In [ ]:
df.row(3, named=True)

#### Indexing

As mentioned earlier, there is no explicit index for a row in polars in constrast to pandas. However, as we just saw, you can use access a row by its position. If you wish to materialize this index, you can do this using the `with_row_index` method. This is not generally necessary and can clutter your dataframe.

In [ ]:
df.with_row_index(name="ind")

### Inspecting Dataframes

While looking at individual rows or slices of a dataframe can be helpful, there are also methods to understand the structure of a dataframe or provide an overview. In the notebook, we can see the column names for a dataframe in the output, but we can also access these columns directly via the `columns` attribute. The `schema` property stores the names of the columns along with their types.

In [ ]:
df.columns

In [ ]:
df.schema

Like numpy arrays and relational databases, polars keeps a data *type* (or `dtype`) for each column. For numeric types, we have float and int variants using different numbers of bits (e.g. `Int64` or `Float64`), but polars also supports dates, datetimes, strings, and categorical types. The string representation of a Series usually lists its dtype, but you can retrieve it directly (`s.dtype`)

In [ ]:
df["longitude"].dtype

Note that polars will generally balk at mixed types in a series (or column).

In [ ]:
s = pl.Series(["a", 12, 34.5])

However, you can use `strict=False` to force polars to find a type to unify the values. In this case, polars converts all of the values to strings and uses a `String` dtype.

In [ ]:
s = pl.Series(["a", 12, 34.5], strict=False)
s.dtype, [type(d) for d in s]

### Dataframe Overview

While the standard dataframe output is often good enough to undersand the contents of the dataframe and see example values, `glimpse()` gives a horizontally-oriented overview can be useful for plain text output. It shows the row and column count as well as the name, type, and sample values for each column. The `max_items_per_column` parameter limits the number of sample values.

In [ ]:
df.glimpse(max_items_per_column=4)

To see statistics about the dataframe columns, use the `describe` method.

In [ ]:
df.describe()

Notice that there are a number of different statistics that are calculated, but some only apply to numeric columns, meaning that non-numeric columns have null entries for quartiles, mean, and standard deviation.

### Modifying the Schema

In some cases, we may wish to update the schema by changing either the names or types of columns. Renaming columns can be done using the `rename` method which takes a dictionary mapping old column names to new ones and returns a new dataframe with the updated scema.

In [ ]:
df = df.rename({"license_": "license"})

We can also convert between types when appropriate using the `cast` method. For a Series, this requires just the type, but for a DataFrame, we pass a dictionary with the column-dtype pairs.

##### Exercise

Try converting the `zip` and `violations` columns to the `Int32` type. Your code should not work--that's ok. Why do you think this happens? Does one of the columns succeed?

In [ ]:
# Your code here

##### Solution

In [ ]:
df.cast({"zip": pl.Int32, "violations": pl.Int32})

We can see that it is not possible to convert many of the violation strings to integers.

In [ ]:
df.cast({"zip": pl.Int32})

### Nullable Types

Every type in polars is nullable, unlike numpy-based pandas. Thus, even though `license` is an integer, there are three null values in that column. There is a validity bitmap stored for each column. 

In [ ]:
df["license"].describe()

### Timestamps

polars also supports datetime values. There are a number of formats for dates and times, and polars can convert well-structured strings to `Datetime` types automatically using casting. In other cases, specific `str.to_datetime` methods may require the format keyword argument to properly parse. Note that polars uses a slightly different language for specifying the format than python so consult the [documentation](https://docs.rs/chrono/latest/chrono/format/strftime/index.html).

In [ ]:
df["inspection_date"].cast(pl.Datetime)

In [ ]:
df["inspection_date"].str.to_datetime(format="%Y-%m-%dT%H:%M:%S%.3f")


### Updating Dataframes

To update a dataframe, we use the `with_columns` method. This method takes a variable number of arguments, all of which are expressions that can create or modify columns. Note, however, that we use the `pl.col` object to distinguish any column in these expressions. For commonly-used columns, we could create a variable to specify that column object, although this can be more difficult for others to read.

In [ ]:
insp_date = pl.col("inspection_date")

Then, we operate on that column. So to update the inspection date column, we could use the `cast` operator in an expression.

In [ ]:
df.with_columns(pl.col("inspection_date").cast(pl.Datetime))

In [ ]:
df.with_columns(insp_date.cast(pl.Datetime))

This method returns a **new** dataframe. While this may seem like it could take a lot of memory, you should not worry about this because polars uses a copy-on-write mechanism that ensures that new columns are created only when something changes. We can also create a new column by using the `alias` modifier. This will maintain the original column and add the modified column with a new name.

In [ ]:
df.with_columns(pl.col("inspection_date").cast(pl.Datetime).alias("inspection_date_dt"))

We will replace our original dataframe with the one with the parsed date.

In [ ]:
df = df.with_columns(pl.col("inspection_date").cast(pl.Datetime))

### Derived Data

In addition to converting columns, we can also create new columns from existing columns via operations. For example, we might wish to construct an `full_address` column that combines the `address`, `city`, `state`, and `zip` columns. In this case, `+` functions as concatenation. For numeric columns, we could use other arithmetic operators to compute derived columns.

In [ ]:
df.with_columns(
    (
        pl.col("address")
        + "\n"
        + pl.col("city")
        + ", "
        + pl.col("state")
        + " "
        + pl.col("zip").cast(pl.String)
    ).alias("full_address")
)

### Queries

With some initial processing completed, we can begin our analysis of the data. We have already seen how pandas allows us to select rows using positions, but we can also filter our dataframe to those values that match particular criteria using the `filter` method. For example, if we want to find all the inspections that were given a pass, we could do that with the boolean expression `pl.col("results") == 'Pass'`. This works because the boolean operations are applied to every item in the column, resulting in a new boolean mask. That sequence of True and False values is used to pull out the correct rows.

In [ ]:
df.filter(pl.col("results") == "Pass")

### Boolean Comparators & Operators

Suppose we are interested in all the inspections that received a pass in the 60608 zip code. Python's normal comparators (`>`, `<`, `>=`, `<=`, `==`, `!=`) can be used directly in column expressions. However, the operators `and`, `or`, and `not` will not work.

In [ ]:
df.filter(pl.col("results") == "Pass" and pl.col("zip") == 60608)

We see the error message points us in the correct direction by suggesting that we use the bitwise operator `&` instead.

In [ ]:
df.filter(pl.col("results") == "Pass" & pl.col("zip") == 60608)

That still doesn't work, but the reason here is that we ensure the boolean comparisons happen first which requires parentheses.

In [ ]:
df.filter((pl.col("results") == "Pass") & (pl.col("zip") == 60608))

##### Exercise

Find all inspections that received a `"Pass"` or `"Pass w/ Conditions"` and were not "Restaurant" facilities.

In [ ]:
# Your code here

##### Solution



In [ ]:
s = df.filter(
    ((pl.col("results") == "Pass") | (pl.col("results") == "Pass w/ Conditions"))
    & ~(pl.col("facility_type") == "Restaurant")
)

### Group By

In order to analyze the results, it can be useful to not only filter them but also to group them. If we only care about the counts of values in each column, we don't need the full `group_by` capabilities. If we want to count the number of inspection results of each type, we can use the `value_counts` method directly on that column:

In [ ]:
df["results"].value_counts()

This returns a dataframe with the results as one column and the count as the other. Note that this is not sorted by default, but we can pass the `sort` argument to recitfy that.

In [ ]:
df["results"].value_counts(sort=True)

The more powerful `group_by` method allows a wide variety of aggregations specified using expressions, but we can emulate the `value_counts` method using the `len()` aggregation.

In [ ]:
df.group_by("results").len()

##### Exercise

What if we want to count by both the `inspection_type` and `results`? Try out different methods to achieve this. What works and what doesn't?

##### Solution

In [ ]:
df[["inspection_type", "results"]].value_counts()  # does not work

In [ ]:
df.select("inspection_type", "results").value_counts()  # does not work

In [ ]:
df.group_by("inspection_type", "results").len()  # works

In [ ]:
df.group_by(["inspection_type", "results"]).len()  # also works

#### Aggregations

Counting can help in some cases, but we might want to perform some statistics on the columns as well. This dataset doesn't have a lot of quantitative values, but the `inspection_date` is one that we can use. For example, we might compute the mean inspection date for a given zip code. To to this, we use `group_by` followed by the `agg` method where we can specify expressions that specify how the results for each group are returned.

Some common aggregation functions are: 
- `len()` (count of how many items are in the group)
- `sum()`
- `min()` and `max()`
- `mean()`
- `median()`
- `std()` (standard deviation)
- `var()` (variance)

In [ ]:
df.group_by("zip").agg(pl.col("inspection_date").mean())

This isn't all that useful on its own, however, because we don't know if those zip codes that seemingly aren't inspected often or are typos or devoid of food establishments. We'd like to have both the mean and the count. We can add a second expression to the `agg` method and then sort the final result by the number of results.

In [ ]:
df.group_by("zip").agg(pl.col("inspection_date").mean(), pl.col("results").len()).sort(
    "results", descending=True
)

We could also include the maximum inspection date from this part of the dataset:

In [ ]:
df.group_by("zip").agg(
    pl.col("inspection_date").mean(),
    pl.col("inspection_date").max(),
    pl.col("results").len(),
)

This causes an error because by default, the aggregation will try to name the result of both the `mean` and `max` expression to the same thing. We can use `alias` to resolve this:

In [ ]:
df.group_by("zip").agg(
    pl.col("inspection_date").mean().alias("mean_inspection_date"),
    pl.col("inspection_date").max().alias("max_inspection_date"),
    pl.col("results").len(),
).sort("results", descending=True)

If you do not specifiy an aggregation, polars will add **all** values from that group as a list. Here, we also use an *expression* in the group by that extracts the year from the inspection date using the `dt` accessor.

In [ ]:
df.filter(pl.col("license") == 2517129).group_by(
    pl.col("inspection_date").dt.year().alias("inspection_year")
).agg(pl.col("results")).sort("inspection_year")

##### Exercise

For each year starting in 2019, find the number of facilities for each risk level that passed with conditions. Ignore those risk levels that do not start with the text `"Risk"`

In [ ]:
# Your code here

##### Solution

In [ ]:
df.filter(pl.col("risk").str.starts_with("Risk")).group_by(
    pl.col("inspection_date").dt.year().alias("inspection_year"), "risk"
).agg(pl.col("results").len()).filter(pl.col("inspection_year") >= 2019).sort(
    "inspection_year", "risk"
)

### String Processing

A key feature of polars is its ability to apply string methods to entire columns. The method for doing this uses python's extensible accessors which serve to allow libraries to add their own "namespaces" to polars objects. The `str` accessor is built-in and provides string methods for polars. Many of these methods align with methods that exist for python string objects while others integrate functionality offered by regular expressions.

If we just search for locations named `"McDonald's"`, we find far fewer inspections than we would expect.

In [ ]:
df.filter(pl.col("dba_name") == "McDonald's")

Looking back at the dataset, you might notice that the names of establishments are generally in all caps. We can match against the captialized version by transforming all of the names to uppercase. Note that the name of this method differs from python's `string.upper`, using the more verbose `str.to_uppercase`.

In [ ]:
df.filter(pl.col("dba_name").str.to_uppercase() == "MCDONALD'S")

That's better but still seems like too few results over an almost four-year period. This might be because there are extra characters in the name (e.g. "McDonald's #11290" or "McDonald's Restaurant"). The `contains_any` method will allow McDonald's to appear anywhere and has an `ascii_case_insensitive` flag that allows us to ignore casing.

In [ ]:
df.filter(
    pl.col("dba_name").str.contains_any(["mcdonald's"], ascii_case_insensitive=True)
)

Now, we might wonder if there are some locations where the apostrophe is dropped (McDonalds). In this case, we could search for those specifically, but we could also create a **regular expression** that specifies the possibility--but not requirement--of an apostrophe. Learning regular expressions takes some time, but mastering them provides important tools for pattern matching. Even if you have used them, a reference for all of the special characters can be useful. *Note:* polars uses Rust's regex syntax which changes a few things from python's `re` library and is not quite as advanced. See the [Rust documentation](https://docs.rs/regex/latest/regex/). For us, `'?` indicates that there exist zero or one apostrophe between final 'd' and 's', and `(?i)` sets the case-insensitive flag. We use the `contains` method for regular expression searches.

In [ ]:
mcds = df.filter(pl.col("dba_name").str.contains("(?i)mcdonald'?s"))

We can count how many times each version of the name is used using `value_counts`, but we can also look at the number of unique names using `n_unique()`

In [ ]:
mcds["dba_name"].value_counts(sort=True)

In [ ]:
mcds["dba_name"].n_unique()

### Data Transformation

A key component of a failed inspection is understanding the types of violations that the inspector found. In our data, this is all packed into the `violations` column. Let's look at this string from a specific inspection using the textwrap module to break up the long string.

In [ ]:
import textwrap

textwrap.wrap(df.filter(pl.col("inspection_id") == 2498181)["violations"][0])

##### Exercise

Try to determine what the format of the violations string is by looking at other examples. First, think about how you might find inspections that have violations and then look at a few of them to see if you can observe a pattern.

##### Solution

We can use a query to find inspections where the results was "Fail" or look for inspections where the violations column is not empty.

In [ ]:
df.filter(pl.col("results") == "Fail").select("violations")

In [ ]:
violations = (
    df.filter(pl.col("results") == "Fail")
    .select("violations")
    .filter(pl.col("violations").is_not_null())
)["violations"]

In [ ]:
textwrap.wrap(violations[0])

After examining a few of these, we might notice that there seems to be a pattern where there are a numbered rules, where each is followed by a dash and then comments about how the rule was violated, and rules are separated by the `|` symbol.

#### More String Methods

With this in mind, we can use some string methods that expand a string to a list of strings. Recall that the `split` method does just that for a given delimiter.

In [ ]:
violations = df.with_columns(pl.col("violations").str.split("|"))["violations"]

Now each entry in our column is a (possibly null) list of strings. If our goal is to analyze the types of violations, we might wish to separate the individual violations out into the violation number, the violation text, and the comments about the violation. The first step is to separate the violations. We can use the `explode` method to separate each violation into a new row and use `drop_nulls` to get rid of empty rows.

In [ ]:
violations = violations.explode().drop_nulls()

Now, our goal is to separate each of these into the three pieces of information:

1. violation number
2. violation text
3. comments

Let's start with the violation number. It is a number followed by a dot. we could potentially use that dot to split the string again. We'd only want to split **once** however so we will use `splitn` with the `n` parameter to limit the number of splits.

In [ ]:
violations.str.splitn(".", n=2)

This produces a struct which means that we have names for the different fields. We can unnest this structure into different columns.

In [ ]:
violations.str.splitn(".", n=2).struct.unnest()

These field names are not very descriptive so we can rename them.

In [ ]:
violations = (
    violations.str.splitn(".", n=2)
    .struct.unnest()
    .rename({"field_0": "violation_number", "field_1": "rest"})
)

##### Exercise

Convert the violation number to an integer. Note that you will have to find a way to strip the whitespace from the beginning of the strings. Also strip the whitespace from the other column.

In [ ]:
# Your code here

##### Solution

In [ ]:
violations = violations.with_columns(
    pl.col("violation_number").str.strip_chars().cast(pl.Int32),
    pl.col("rest").str.strip_chars(),
)

#### Back to Regular Expressions

Another string method that polars has related to regular expressions is the `extract` method. We could have used it to construct a pattern to extract the violation number instead. The parentheses indicate the portion of the pattern we wish to capture.

In [ ]:
violations = (
    df.with_columns(pl.col("violations").str.split("|"))["violations"]
    .explode()
    .drop_nulls()
)
violations.str.extract(r"^\s*(\d+)\.")

These can be converted to integers immediately since we did not include the spaces in our extraction.

In [ ]:
violations.str.extract(r"^\s*(\d+)\.").cast(pl.Int32)

We can use this this strategy to extract both parts of the regular expression. Now, we can ask for the groups individually and name them.

In [ ]:
pattern = r"(\d+)\.\s*(.*)"

violation_details = violations.to_frame().select(
    pl.col("violations")
    .str.extract(pattern, 1)
    .cast(pl.Int32)
    .alias("violation_number"),
    pl.col("violations").str.extract(pattern, 2).alias("rest"),
)

### Final Exercises

1. All right, we've started attacking our problem but we haven't finished it. It's now up to you to extract all three columns (violation_num, violation_text, comments) for all of the violations. Be careful. A few violations have no comments.

2. Now, determine which violation is **most frequent**. But before you do that, note that the violation numbers changed at some point in the past. Read through the [metadata](https://data.cityofchicago.org/Health-Human-Services/Food-Inspections/4ijn-s7e5/about_data) to learn more. So you will need to split the violations into two groups and find the most frequent one across both groups.

### Conditional Statements

Similar to native python's `if`,`elif` and `else`, Polars offer a similar conditional selection. This is like a ternary operator through the function `when`, which is followed by function `then` and an optional function `otherwise`.  

- `when`: Accepts a expression or the condition upon which a column is evaluated.
- `then`: Contains an expression which is replaced when the expression in `when` evaluates to **True**.
- `otherwise`:  Contains an expression which is replaced when the expression in `when` evaluates to **False**.

In this case, we are just assigning an "A" or an "F" as literal values, but we coul;d use any expression here, involving other columns.

In [ ]:
df.select(
    pl.col("dba_name"),
    pl.when(pl.col("results") == "Pass")
    .then(pl.lit("A"))
    .otherwise(pl.lit("F"))
    .alias("inspection_grade"),
)

### Lazy vs. Eager Evaluation

Polars supports two modes of operation: 
 - *lazy*: Waits on execution until all the steps are defined and `collect` is called. This allows a query planner to perform optimizations.
 - *eager* Every step is executed immediately returning the intermediate results. This could be less efficient since we might do unnecessary computations.

Lets see how a lazy expression can potentially help for large computations. Many of the readers have lazy `scan_*` versions that may not need to read the entire dataset or pull everything into memory in order to run the computation.

In [ ]:
df = pl.scan_csv("Food_Inspections.csv.gz")

Notice that this call does not produce a result. It simply says something about a plan. If we write the rest of the query, polars will continue to add to the plan.

In [ ]:
df.filter(pl.col("facility_type") == "School").select(
    ["aka_name", "facility_type", "risk"]
)

When we call `collect()`, polars will execute the read plus the operations we have added.

In [ ]:
df.filter(pl.col("facility_type") == "School").select(
    ["aka_name", "facility_type", "risk"]
).collect()